<br>
# 1. naver news crawling

In [2]:
import re
import pandas as pd
from bs4 import BeautifulSoup
import requests
import numpy as np
from urllib.parse import quote
import pickle
import random
from __future__ import print_function
from newspaper import Article
import csv

<bs>
## 1-1. article crawling: day

In [3]:
def get_article(date):
    total = []
    
    pages = ['1']
    for page in pages:
        session = requests.Session()
        headers = {"User-Agent": "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_9_5) AppleWebKit537.36 (KHTML, like Gecko) Chrome", "Accept": "text/html,application/xhtml+xml,application/xml;q=0.9,image/webp,*/*;q=0.8"}
        page_url = 'http://news.naver.com/main/list.nhn?mode=LS2D&mid=shm&sid2=264&sid1=100&date={}&page={}'.format(date, page)       
        r = session.get(page_url, headers=headers)
        soup = BeautifulSoup(r.text, 'html.parser')
        dl_list = soup.find('div', {'class':'list_body newsflash_body'}).findAll('dl')
        
        i = 0
        while i < len(dl_list):
            dl = dl_list[i]
            article_url = dl.findAll('dt')[-1].find('a')['href'] 
            article_cont = Article(article_url, language='ko')
            article_cont.download()
            try:  
                article_cont.parse()
                article_title = article_cont.title
                article_cont = article_cont.text.replace("\t","").replace("\n","").replace("\r","")
                total.append([article_title, article_cont])

            except:
                i -= 1
            i += 1   
    
        if page == '1':
            try:
                page_range = soup.find('div', {'class':'paging'}).findAll('a')
                page_range = [t.text for t in page_range if t.text != '다음']
                pages += page_range
                
            except:
                pages = pages
        
    return pd.DataFrame(total, columns = ['article_title', 'article_cont'])

In [33]:
get_article('20180105')

AttributeError: 'NoneType' object has no attribute 'findAll'

<bs>
## 1-2. article crawling: month

In [4]:
def get_all_article(date_list):
    total = pd.DataFrame()
    
    for date in date_list:
        date_article = get_article(date)
        total = pd.concat([total, date_article], ignore_index=True)
    
    return total

In [5]:
def make_date_list(month):
    month_28 = ['02']
    month_30 = ['04', '06', '09', '11']
    month_31 = ['01', '03', '05', '07', '08', '10', '12']

    date_range = ['0'+str(i) for i in range(1,10)] + [str(i) for i in range(10,32)]

    if month in month_28:
        date_list = ['2017'+month+t for t in date_range[:28]]    
    elif month in month_30:
        date_list = ['2017'+month+t for t in date_range[:30]]
    elif month in month_31:
        date_list = ['2017'+month+t for t in date_range[:31]]
        
    return date_list

In [12]:
article_201703 = get_all_article(make_date_list('03'))
article_201703

article_title  \
0                                   광화문 탄핵 찬성과 반대   
1                                   광화문 탄핵 찬성과 반대   
2            3.1절 차벽 두고 맞선 촛불-태극기…충돌 없이 마무리(종합2보)   
3                                        탄핵 찬성 촛불   
4                                           촛불 행진   
5                                        탄핵 찬성 촛불   
6                                        광장 메운 촛불   
7                                          빗 속 촛불   
8                                          빗 속 촛불   
9                                         3.1절 촛불   
10                                        3.1절 촛불   
11                                        3.1절 촛불   
12                                    경찰 차벽 뒤로 촛불   
13                                        3.1절 촛불   
14                                        3.1절 촛불   
15                             '비가 내려도 꺼지지 않는 촛불'   
16                                    '꺼지지 않는 촛불'   
17                         '비바람 몰아쳐도 촛불은 꺼지지 않는다'   
18                               '오늘도 외친다 대통령 탄핵'   
19                               '광화문광장 가득 채운 촛불'   
20                             '비가 내려도 꺼지지 않는 촛불'   
21                           '비가 내려도 촛불은 꺼지지 않는다'   
22                              '비가 와도 꺼지지 않는 촛불'   
23                                          촛불 기둥   
24                                          촛불 기둥   
25                                          빗속 촛불   
26                                       해산하는 태극기   
27                               모이는 촛불, 해산하는 태극기   
28                                       해산하는 태극기   
29                           '불 밝히는 촛불, 해산하는 태극기'   
...                                           ...   
3735                      제19대 대통령 재외선거 안내판 걸린 공항   
3736     민주당 "주범이자 피의자" 구속 촉구…윤상현 "국민 통합 위해 기각돼야"   
3737                                    '전두환 회고록'   
3738              박 전 대통령 오전 영장심문 종료…오후 2시 재개(종합)   
3739                  박 전 대통령 오전 영장심문 종료…오후 2시 재개   
3740        전두환 "최태민, 박근혜 업고 많은 물의…10·26後 군부대 격리"   
3741   [단독] 전두환 "최태민, 박근혜 업고 많은 물의…10·26後 군부대 격리"   
3742            朴전대통령 '靑근처 얼씬말라'고 했던 동생과 '눈물의 재회'   
3743        [朴 전 대통령 영장심사]"발부" vs "기각" 법조계 의견도 분분   
3744              '창-방패' 재격돌…'朴 뇌물죄' 치열한 법정공방(종합)   
3745             [영상]'피의자 박근혜' 영장실질심사 출두현장 '굳은표정'   
3746     [MusT]"아이 진짜" 카메라 안 잡히려 노력…朴 전 대통령 법원 출석   
3747                                 박근혜 '착잡한 마음'   
3748                                     태극기와 박근혜   
3749                                     박근혜 '손짓'   
3750        朴전대통령, 자택 찾은 親朴 인사들에 "나 때문에 미안하다"(종합)   
3751       한웅재·이원석 vs 유영하·채명성 '격돌'…심판은 강부영 판사(종합)   
3752                   朴 전 대통령 구속 기로에…靑 "참담하고 비통"   
3753             '수인번호 503' 박근혜, 3평짜리 독방 쓴다(종합2보)   
3754      박근혜 前대통령 6명 쓰는 3.2평 방 혼자 쓴다…'예우' 차원(종합)   
3755             [연합시론] 박근혜 시대의 종언, 이제 미래를 얘기할 때다   
3756               박근혜 영장 발부에서 구치소 출발까지 90분…무슨 일?   
3757               [영상] 박근혜는 구치소, 세월호는 목포 '엇갈린 길'   
3758          박근혜 前대통령 6명 쓰는 3.2평 방 혼자 쓴다…'예우' 차원   
3759           [박근혜 구속]'잠수 탄' 박근혜 변호인들…유영하 구치소 방문   
3760             '이재용, 朴-崔 관계 알았나'…삼성-특검 정면대립(종합)   
3761  [박 前대통령 구속]영애에서 대통령, 그리고 피의자로…‘비극의 정치사’ 쓴 朴   
3762               [종합]안철수 "朴사면? 남용 못하도록 위원회서 논의"   
3763             [박근혜 구속] 北 관영매체, 13시간만에 첫 보도(종합)   
3764                   '천민'에서 대권주자로, 홍준표의 투쟁기(종합)   

                                           article_cont  
0     【서울=뉴시스】사진공동취재단 = 3.1절인 1일 서울광장과 광화문 인근 등 서울 도...  
1     【서울=뉴시스】사진공동취재단 = 3.1절인 1일 서울광장과 광화문 인근 등 서울 도...  
2     3.1운동 98주년을 맞은 1일 오후 서울 세종대로 사거리와 광화문광장에서 각각 탄...  
3     【서울=뉴시스】최동준 기자 = 1일 서울 광화문 광장에서 열린 박근혜 대통령 퇴진 ...  
4     【서울=뉴시스】최동준 기자 = 1일 서울 광화문 광장에서 열린 박근혜 대통령 퇴진 ...  
5     【서울=뉴시스】최동준 기자 = 1일 서울 광화문 광장에서 열린 박근혜 대통령 퇴진 ...  
6     【서울=뉴시스】사진공동취재단 = 박근혜정권 퇴진 비상국민행동’(퇴진행동)은 1일 오...  
7     【서울=뉴시스】사진공동취재단 = 박근혜정권 퇴진 비상국민행동’(퇴진행동)은 1일 오...  
8     【서울=뉴시스】사진공동취재단 = 박근혜정권 퇴진 비상국민행동’(퇴진행동)은 1일 오...  
9     【서울=뉴시스】사진공동취재단 = 박근혜정권 퇴진 비상국민행동’(퇴진행동)은 1일 오...  
10    【서울=뉴시스】사진공동취재단 = 박근혜정권 퇴진 비상국민행동’(퇴진행동)은 1일 오...  
11    【서울=뉴시스】사진공동취재단 = 박근혜정권 퇴진 비상국민행동’(퇴진행동)은 1일 오.

In [13]:
f = open('article_201703.txt', 'wb')
pickle.dump(article_201703, f)
f.close()

In [14]:
a = open('article_201703.txt', "rb")
pickle.load(a)

article_title  \
0                                   광화문 탄핵 찬성과 반대   
1                                   광화문 탄핵 찬성과 반대   
2            3.1절 차벽 두고 맞선 촛불-태극기…충돌 없이 마무리(종합2보)   
3                                        탄핵 찬성 촛불   
4                                           촛불 행진   
5                                        탄핵 찬성 촛불   
6                                        광장 메운 촛불   
7                                          빗 속 촛불   
8                                          빗 속 촛불   
9                                         3.1절 촛불   
10                                        3.1절 촛불   
11                                        3.1절 촛불   
12                                    경찰 차벽 뒤로 촛불   
13                                        3.1절 촛불   
14                                        3.1절 촛불   
15                             '비가 내려도 꺼지지 않는 촛불'   
16                                    '꺼지지 않는 촛불'   
17                         '비바람 몰아쳐도 촛불은 꺼지지 않는다'   
18                               '오늘도 외친다 대통령 탄핵'   
19                               '광화문광장 가득 채운 촛불'   
20                             '비가 내려도 꺼지지 않는 촛불'   
21                           '비가 내려도 촛불은 꺼지지 않는다'   
22                              '비가 와도 꺼지지 않는 촛불'   
23                                          촛불 기둥   
24                                          촛불 기둥   
25                                          빗속 촛불   
26                                       해산하는 태극기   
27                               모이는 촛불, 해산하는 태극기   
28                                       해산하는 태극기   
29                           '불 밝히는 촛불, 해산하는 태극기'   
...                                           ...   
3735                      제19대 대통령 재외선거 안내판 걸린 공항   
3736     민주당 "주범이자 피의자" 구속 촉구…윤상현 "국민 통합 위해 기각돼야"   
3737                                    '전두환 회고록'   
3738              박 전 대통령 오전 영장심문 종료…오후 2시 재개(종합)   
3739                  박 전 대통령 오전 영장심문 종료…오후 2시 재개   
3740        전두환 "최태민, 박근혜 업고 많은 물의…10·26後 군부대 격리"   
3741   [단독] 전두환 "최태민, 박근혜 업고 많은 물의…10·26後 군부대 격리"   
3742            朴전대통령 '靑근처 얼씬말라'고 했던 동생과 '눈물의 재회'   
3743        [朴 전 대통령 영장심사]"발부" vs "기각" 법조계 의견도 분분   
3744              '창-방패' 재격돌…'朴 뇌물죄' 치열한 법정공방(종합)   
3745             [영상]'피의자 박근혜' 영장실질심사 출두현장 '굳은표정'   
3746     [MusT]"아이 진짜" 카메라 안 잡히려 노력…朴 전 대통령 법원 출석   
3747                                 박근혜 '착잡한 마음'   
3748                                     태극기와 박근혜   
3749                                     박근혜 '손짓'   
3750        朴전대통령, 자택 찾은 親朴 인사들에 "나 때문에 미안하다"(종합)   
3751       한웅재·이원석 vs 유영하·채명성 '격돌'…심판은 강부영 판사(종합)   
3752                   朴 전 대통령 구속 기로에…靑 "참담하고 비통"   
3753             '수인번호 503' 박근혜, 3평짜리 독방 쓴다(종합2보)   
3754      박근혜 前대통령 6명 쓰는 3.2평 방 혼자 쓴다…'예우' 차원(종합)   
3755             [연합시론] 박근혜 시대의 종언, 이제 미래를 얘기할 때다   
3756               박근혜 영장 발부에서 구치소 출발까지 90분…무슨 일?   
3757               [영상] 박근혜는 구치소, 세월호는 목포 '엇갈린 길'   
3758          박근혜 前대통령 6명 쓰는 3.2평 방 혼자 쓴다…'예우' 차원   
3759           [박근혜 구속]'잠수 탄' 박근혜 변호인들…유영하 구치소 방문   
3760             '이재용, 朴-崔 관계 알았나'…삼성-특검 정면대립(종합)   
3761  [박 前대통령 구속]영애에서 대통령, 그리고 피의자로…‘비극의 정치사’ 쓴 朴   
3762               [종합]안철수 "朴사면? 남용 못하도록 위원회서 논의"   
3763             [박근혜 구속] 北 관영매체, 13시간만에 첫 보도(종합)   
3764                   '천민'에서 대권주자로, 홍준표의 투쟁기(종합)   

                                           article_cont  
0     【서울=뉴시스】사진공동취재단 = 3.1절인 1일 서울광장과 광화문 인근 등 서울 도...  
1     【서울=뉴시스】사진공동취재단 = 3.1절인 1일 서울광장과 광화문 인근 등 서울 도...  
2     3.1운동 98주년을 맞은 1일 오후 서울 세종대로 사거리와 광화문광장에서 각각 탄...  
3     【서울=뉴시스】최동준 기자 = 1일 서울 광화문 광장에서 열린 박근혜 대통령 퇴진 ...  
4     【서울=뉴시스】최동준 기자 = 1일 서울 광화문 광장에서 열린 박근혜 대통령 퇴진 ...  
5     【서울=뉴시스】최동준 기자 = 1일 서울 광화문 광장에서 열린 박근혜 대통령 퇴진 ...  
6     【서울=뉴시스】사진공동취재단 = 박근혜정권 퇴진 비상국민행동’(퇴진행동)은 1일 오...  
7     【서울=뉴시스】사진공동취재단 = 박근혜정권 퇴진 비상국민행동’(퇴진행동)은 1일 오...  
8     【서울=뉴시스】사진공동취재단 = 박근혜정권 퇴진 비상국민행동’(퇴진행동)은 1일 오...  
9     【서울=뉴시스】사진공동취재단 = 박근혜정권 퇴진 비상국민행동’(퇴진행동)은 1일 오...  
10    【서울=뉴시스】사진공동취재단 = 박근혜정권 퇴진 비상국민행동’(퇴진행동)은 1일 오...  
11    【서울=뉴시스】사진공동취재단 = 박근혜정권 퇴진 비상국민행동’(퇴진행동)은 1일 오.

<bs>
## 1-3. article crawling: year

In [ ]:
def get_year_article(month_list):
    article_2017 = pd.DataFrame()
    for month in month_list:
        month_article = pd.read_pickle('article_2017'+month+'.txt')
        article_2017 = pd.concat([article_2017, month_article], ignore_index=True)
        
    return article_2017

In [ ]:
month_list = ['0'+str(i) for i in range(1,10)] + [str(i) for i in range(10,13)]
month_list

In [ ]:
article_2017 = get_year_article(month_list)
article_2017

In [ ]:
#error 제거
error_date = ['2017.12.23. 11:30 ~ 14:30', '2017.12.24. 05:30 ~ 08:30', '2017.12.23. 17:30 ~ 20:30', '2017.12.23. 20:30 ~ 23:30', '2017.12.24. 08:30 ~ 11:30']
error = ['8765432187654321876543218765432187654321876543218765432187654321스포츠연예IT/과학세계생활/문화사회경제정치다음이전검색어 입력||검색어 입력핫이슈뉴스토픽추출이 일시적으로 늦어져 최신 정보를 제공할 수 없습니다. {} 기준도움말'.format(t) for t in error_date]
error

In [ ]:
error_location = [t not in error for t in article_2017.article_cont]
error_location

In [ ]:
article_2017 = article_2017[error_location]
article_2017.index = np.arange(31513)
article_2017

In [ ]:
f = open('article_2017.txt', 'wb')
pickle.dump(article_2017, f)
f.close()

In [ ]:
a = open('article_2017.txt', "rb")
article_2017 = pickle.load(a)
article_2017

In [ ]:
article_2017.to_csv('article_2017.csv', index=False)

In [ ]:
article_2017 = pd.read_csv('article_2017.csv', encoding='cp949')
article_2017

<br><br>
# 2. extract summarization: lexrank&textrank

In [ ]:
from lexrankr import LexRank
from gensim.summarization import summarize

In [ ]:
lexrank = LexRank()

In [ ]:
def get_summarization(article_df, line_num, word_count):
    total_sum = []
    sum_type = []
    for i in range(len(article_df)):
        if i%500==0:
            print(i)
        
        article = article_df.article_cont[i]
        if article[0] == '[':
            try:
                finish = article.index(']')+1
                remove_str = article[:finish]
                article = article.replace(remove_str,"")
                
            except:
                article = article
        
        try:
            lexrank.summarize(article)
            summarization = lexrank.probe(line_num) #lexrank
            summarization = summarization[0]+" "+summarization[1]
            sum_textrank = summarize(article, word_count=word_count) #textrank
            
            if len(sum_textrank)>0 and len(summarization)>len(sum_textrank):
                summarization = sum_textrank
                sum_type.append("textrank")
            else:
                sum_type.append("lexrank")
            
            summarization = re.sub('[-=#\/:$()\[\]\"}]', '', summarization)
            summarization = re.sub("[\'!?\.\,·◇△]", '', summarization)
            summarization = summarization.replace("\n","").replace("기자","")
            
            total_sum.append(summarization)
                
        except:
            summarization = article
            summarization = re.sub('[-=#/:$()\\[\\]\\"}]', '', summarization)
            summarization = re.sub("[\'!?\.\,·◇△]", '', summarization)
            summarization = summarization.replace("\n","").replace("기자","")
            
            total_sum.append(summarization)
            sum_type.append("article_cont")

    total_sum = pd.DataFrame(total_sum, columns=['summarization'])
    sum_type = pd.DataFrame(sum_type, columns=['sum_type'])
    
    return pd.concat([article_df, total_sum, sum_type], axis=1)

In [ ]:
summarization_df = get_summarization(article_2017, 2, 50)
summarization_df

In [ ]:
sum(list(summarization_df.sum_type!="article_cont"))

In [ ]:
f = open('article_final_data.txt', 'wb')
pickle.dump(summarization_df, f)
f.close()

In [ ]:
a = open('article_final_data.txt', "rb")
sum_df = pickle.load(a)

In [ ]:
summarization_df.to_csv("article_final_data.csv", index=False)

In [ ]:
pd.read_csv("article_final_data.csv", encoding="cp949")

<br><br>
# 3. POS tagging: NN(명), NR(수), VV(동), VA(형)

In [ ]:
import pickle
import pandas as pd
import numpy

In [ ]:
from konlpy.tag import Kkma
kkma = Kkma()

In [ ]:
a = open('article_only_summarization.txt','rb')
sum_df = pickle.load(a)
sum_df

In [ ]:
def make_pos(sum_df):
    pos_titles = pd.DataFrame([0]*len(sum_df), columns=['pos_title'])
    pos_articles = pd.DataFrame([0]*len(sum_df), columns=['pos_article'])
    pos_sums = pd.DataFrame([0]*len(sum_df), columns=['pos_sum'])
    
    for i in range(len(sum_df)):
        pos_title = kkma.pos(sum_df.article_title[i])
        pos_article = kkma.pos(sum_df.article_cont[i])
        pos_sum = kkma.pos(sum_df.summarization[i])
        
        pos_title = [t for t in pos_title if t[1][0:2] in ["NN","NR","VV","VA"]]
        pos_article = [t for t in pos_article if t[1][0:2] in ["NN","NR","VV","VA"]]
        pos_sum = [t for t in pos_sum if t[1][0:2] in ["NN","NR","VV","VA"]]
    
        pos_titles.pos_title[i] = pos_title
        pos_articles.pos_article[i] = pos_article
        pos_sums.pos_sum[i] = pos_sum
        
    return pd.concat([pos_titles, pos_articles, pos_sums], axis=1)

In [ ]:
sum_pos = make_pos(sum_df)
sum_pos

In [ ]:
kk = []
for kkk in sum_pos.pos_sum:
    kk = kk+kkk
len(set(kk))

In [ ]:
f = open('summarization_pos.txt', 'wb')
pickle.dump(sum_pos, f)
f.close()

In [2]:
a = open('summarization_pos.txt', 'rb')
sum_pos = pickle.load(a)

In [4]:
sum_pos

pos_title  \
0      [(신년사, NNG), (예탁, NNG), (결제, NNG), (원, NNG), (...   
1      [(덕, NNG), (훈, NNG), (행장, NNG), (조선, NNG), (등,...   
2      [(주간, NNG), (추천, NNG), (종목, NNG), (화학, NNG), (...   
3      [(터키, NNG), (나이트, NNG), (클럽, NNG), (총격, NNG), ...   
4      [(멀, VA), (정, NNG), (유년, NNG), (증시, NNG), (힘차,...   
5      [(멀, VA), (코스닥, NNG), (1, NR), (월, NNM), (효과, ...   
6      [(채권, NNG), (주식, NNG), (유동성, NNG), (대전환, NNG),...   
7      [(스타, NNG), (6, NR), (부동산, NNG), (채권, NNG), (뭉...   
8      [(빚, NNG), (테크, NNP), (돈, NNG), (벌, VV), (장기, ...   
9      [(커지, VV), (살, VV), (몸, NNG), (집, NNG), (키우, V...   
10     [(멀, VA), (2017, NR), (정유, NNG), (업종, NNG), (투...   
11     [(정, NNG), (유년, NNG), (새둥지, NNG), (트, VV), (삼성...   
12     [(새해, NNG), (박스, NNG), (피, NNG), (뚫, VV), (에너지...   
13     [(펀드, NNG), (치, NNG), (1, NR), (월, NNM), (효과, ...   
14     [(멀, VA), (글로벌, NNG), (스톡, NNG), (하이드, NNG), (...   
15     [(강, NNG), (달러, NNG), (유지, NNG), (외국인, NNG), (...   
16     [(닭띠, NNG), (광구, NNG), (우리은행, NNG), (장, NNG), ...   
17     [(정, NNG), (유년, NNG), (거취, NNG), (주목, NNG), (붉...   
18     [(명, NNM), (퇴, NNG), (애환, NNG), (거리, NNG), (간판...   
19     [(1, NR), (호, NNM), (증권사, NNG), (교보, NNG), (김,...   
20     [(부럽, VA), (브라질, NNG), (러시아, NNG), (2016, NR),...   
21     [(이번, NNG), (주, NNG), (증시, NNG), (12, NR), (월,...   
22     [(글로벌, NNG), (공략, NNG), (가속화, NNG), (세계, NNG),...   
23     [(트럼프, NNG), (행정부, NNG), (출범, NNG), (앞두, VV), ...   
24     [(재계, NNG), (정, NNG), (유년, NNG), (산, NNG), (너머...   
25     [(전인권, NNG), (신대, NNG), (철, NNG), (아름, NNP), (...   
26     [(닭띠, NNG), (광구, NNG), (우리은행, NNG), (장, NNG), ...   
27     [(정, NNG), (유년, NNG), (거취, NNG), (주목, NNG), (붉...   
28     [(명, NNM), (퇴, NNG), (애환, NNG), (거리, NNG), (간판...   
29     [(1, NR), (호, NNM), (증권사, NNG), (교보, NNG), (김,...   
...                                                  ...   
17649  [(2018, NR), (한국, NNG), (경제, NNG), (경제, NNG), ...   
17650  [(내년, NNG), (중국, NNG), (부동산, NNG), (투자, NNG), ...   
17651  [(다음주, NNG), (코스, NNG), (피, NNG), (2420, NR), ...   
17652  [(뉴욕, NNP), (증시, NNG), (마감, NNG), (크리스마스, NNG)...   
17653  [(뉴욕, NNP), (증시, NNG), (성탄절, NNG), (앞두, VV), (...   
17654  [(뉴욕, NNP), (증시, NNG), (경제, NNG), (지표, NNG), (...   
17655  [(걸, VV), (근공, NNG), (대체, NNG), (투자, NNG), (자문...   
17656  [(진, NNG), (격의, NNG), (롯데, NNP), (칠성, NNG), (음...   
17657  [(건축, NNG), (매각, NNG), (공익, NNG), (채무, NNG), (...   
17658  [(트럼프, NNG), (세제, NNG), (법안, NNG), (서명, NNG), ...   
17659  [(2018, NR), (한국, NNG), (경제, NNG), (경제, NNG), ...   
17660  [(내년, NNG), (중국, NNG), (부동산, NNG), (투자, NNG), ...   
17661  [(다음주, NNG), (코스, NNG), (피, NNG), (2420, NR), ...   
17662  [(뉴욕, NNP), (증시, NNG), (마감, NNG), (크리스마스, NNG)...   
17663  [(뉴욕, NNP), (증시, NNG), (성탄절, NNG), (앞두, VV), (...   
17664  [(뉴욕, NNP), (증시, NNG), (경제, NNG), (지표, NNG), (...   
17665  [(걸, VV), (근공, NNG), (대체, NNG), (투자, NNG), (자문...   
17666  [(진, NNG), (격의, NNG), (롯데, NNP), (칠성, NNG), (음...   
17667  [(건축, NNG), (매각, NNG), (공익, NNG), (채무, NNG), (...   
17668  [(트럼프, NNG), (세제, NNG), (법안, NNG), (서명, NNG), ...   
17669  [(2018, NR), (한국, NNG), (경제, NNG), (경제, NNG), ...   
17670  [(내년, NNG), (중국, NNG), (부동산, NNG), (투자, NNG), ...   
17671  [(다음주, NNG), (코스, NNG), (피, NNG), (2420, NR), ...   
17672  [(뉴욕, NNP), (증시, NNG), (마감, NNG), (크리스마스, NNG)...   
17673  [(뉴욕, NNP), (증시, NNG), (성탄절, NNG), (앞두, VV), (...   
17674  [(뉴욕, NNP), (증시, NNG), (경제, NNG), (지표, NNG), (...   
17675  [(걸, VV), (근공, NNG), (대체, NNG), (투자, NNG), (자문...   
17676  [(진, NNG), (격의, NNG), (롯데, NNP), (칠성, NNG), (음...   
17677  [(건축, NNG), (매각, NNG), (공익, NNG), (채무, NNG), (...   
17678  [(트럼프, NNG), (세제, NNG), (법안, NNG), (서명, NNG), ...   

                                             pos_article  \
0      [(아시아, NNG), (경제, NNG), (박, NNG), (나, VV), (영,...   
1      [(덕, NNG), (훈, NNG), (수출입, NNG), (은행, NNG), (장...   
2      [(김, NNG), (지, NNG), (기자, NNG), (금융, NNG), (투자...   
3      [(이, NNG), (데일리, NNG), (이민, NNG), (정, NNG), (기...   
4      [(코스, NNG), (피, NNG

In [9]:
def make_sum_input(sum_pos):
    input_sums = pd.DataFrame([0]*len(sum_pos), columns=['pos_sum'])
    input_articles = pd.DataFrame([0]*len(sum_pos), columns=['pos_article'])
    
    for i in range(len(sum_pos)):
        pos_sum = ""
        for tag in sum_pos.pos_sum[i]:
            pos_sum = pos_sum + " " +tag[0]
            
        pos_article = ""
        for tag in sum_pos.pos_article[i]:
            pos_article = pos_article + " " +tag[0]
        
        input_sums.pos_sum[i] = pos_sum
        input_articles.pos_article[i] = pos_article

    return pd.concat([input_sums, input_articles], axis=1)

In [13]:
sum_input = make_sum_input(sum_pos)
sum_input

pos_sum  \
0       한국 예탁 결제 원 사장 1 일 신년 사 통하 전자 증권 제도 시행 기반 조성 라...   
1       교자 채신 힘 듣 가깝 곳 멀 곳 땔나무 캐 하 늘 의미 다이 행장 올해 과제 전...   
2       대신 증권 한솔 케미칼 최근 인수 자회사 팩스 이익 반영 수익성 강화 삼성전자 양...   
3       1 일 현지 시간 터키 탄불 오르타 이 인근 나이트 클럽 총격 사건 발생 최소 3...   
4       코스 피 상단 밴드 2150 2350 전망 2017 년 정유 증시 밝 주요 증권사...   
5       반도체 성수기 호재 자율 주행 차 등 성장주 유망 유니 동화 기업 평가 되 종목 ...   
6       따르 내년 삼성전자 추가 급등 국내 주요 기업 지주사 전환 잭 이벤트 예고 곽 현...   
7       김 팀장 중국 일대일 미국 인프라 투자 공약 감안 때 금속 중심 원자재 투자 유효...   
8       전문가 신규 장기 대출 받으 고정 금리 선택 기존 변동 금리 대출 받 고정 금리 ...   
9       8 조 원 이상 종합 금융 투자 계좌 개설 부동산 담보 신탁 업무 하 수 있 따르...   
10      임은 영 삼성 증권 연구원 중국 시장 소형차 구매 세 감면 연장 자동차 금융 비중...   
11      삼성 증권 서초 삼성 타운 이전 완료 강남 시대 자산 관리 역량 극대화 금융 계열...   
12      롯데 케미칼 부타디엔 체인 스프레드 확대 따르 이익 성장 전망 상장 조선사 중 재...   
13      양호 수익률 보이 가운데 브라질 주식 펀드 남미 신흥국 주식 펀드 51 315 오...   
14      해외 매출 비중 14 수준 베트남 중심 동남아 사료 시장 진출 하이드 그룹 어류 ...   
15      달러 강세 외국인 자금 국내 시장 이탈 것 김 성환 부국 증권 연구원 달러 부담 ...   
16      민 영화 성공 후 이 행장 개인적 우리 은행장 연임 새 시험대 앞 서 사외 이사 ...   
17      스마트 근무제 가 보수적 은행 조직 정착 수 있 회의적 시선 많 지난해 11 월 ...   
18      작품 시의 오 공동 당선작 정하 한편 수필 늘 성수 기와 비수기 재래시장 마트 차...   
19      더불 전문 사모 집합 투자업 사모 펀드 업 진출 다양 금융 상품 출시 고객 기반 ...   
20      나라 11 월 달러 부족 사태 통화 가치 48 절하 나이 지리 아 화 368 떨어...   
21      달러 향방 예측 위하 트럼프 재정 정책 연 주 금리 인상 시점 관 환 멘트 주시 ...   
22      세계 1 위 수액 기업 박스 터 생명 과학 영양 수액 기술 사 갈 정도 차 대표 ...   
23      트럼프 랠리 마침표 찍 데 트럼프 행정부 출범 앞두 도 트럼프 대통령 당선자 공약...   
24      현대 기아 차 그룹 올해 자율 주행 차 시대 등 대비 기술 개발 총력 기울이 미래...   
25      20161231 뉴스 1 저작권자 뉴스 1 코리 아 무단 전재 배포 금지 머니 투...   
26      민 영화 성공 후 이 행장 개인적 우리 은행장 연임 새 시험대 앞 서 사외 이사 ...   
27      스마트 근무제 가 보수적 은행 조직 정착 수 있 회의적 시선 많 지난해 11 월 ...   
28      작품 시의 오 공동 당선작 정하 한편 수필 늘 성수 기와 비수기 재래시장 마트 차...   
29      더불 전문 사모 집합 투자업 사모 펀드 업 진출 다양 금융 상품 출시 고객 기반 ...   
...                                                  ...   
17649   지난달 말 기준 금리 인상 기대 시장 금리 상승 점 대출 금리 반영 것 보이 27...   
17650   질적 성장 무게 감 두 방침 하 최 연구원 중국 정부 2020 년 금융 리스크 통...   
17651   투자 증권 다음주 올해 마지막 거래 주간 코스 피 밴드 2420 2480 전망 내...   
17652   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17653   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17654   도 트럼프 대통령 이날 크리스마스 연휴 앞두 세제 법안 서명 22 일 현지 시간 ...   
17655   나이스 피 앤 아이 최대 2019 년 건설 근로자 공제 회의 대체 투자 자문 되 ...   
17656   일각 신 회장 실형 받 경우 오너 부재 따르 악재 자금 조달 부정적 영향 끼치 수...   
17657   법원 빠르 시일 내 매각 내년 2 월 초 회생 계획안 하 계획 가지 것 전하 이번...   
17658   당초 연말 서명 늦추 수 있 전망 크리스마스 연휴 앞두 세제 개혁 마무리 미국인 ...   
17659   지난달 말 기준 금리 인상 기대 시장 금리 상승 점 대출 금리 반영 것 보이 27...   
17660   질적 성장 무게 감 두 방침 하 최 연구원 중국 정부 2020 년 금융 리스크 통...   
17661   투자 증권 다음주 올해 마지막 거래 주간 코스 피 밴드 2420 2480 전망 내...   
17662   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17663   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17664   도 트럼프 대통령 이날 크리스마스 연휴 앞두 세제 법안 서명 22 일 현지 시간 ...   
17665   나이스 피 앤 아이 최대 2019 년 건설 근로자 공제 회의 대체 투자 자문 되 ...   
17666   일각 신 회장 실형 받 경우 오너 부재 따르 악재 자금 조달 부정적 영향 끼치 수...   
17667   법원 빠르 시일 내 매각 내년 2 월 초 회생 계획안 하 계획 가지 것 전하 이번...   
17668   당초 연말 서명 늦추 수 있 전망 크리스마스 연휴 앞두 세제 개혁 마무리 미국인 ...   
17669   지난달 말 기준 금리 인상 기대 시장 금리 상승 점 대출 금리 반영 것 보이 27...   
17670   질적 성장 무게 감 두 방침 하 최 연구원 중국 정부 2020 년 금융 리스크 통...   
17671   배당 수익률 상위 종목 산 46 메 리 종 금 증권 46 기업 은행 44 효성 4...   
17672   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17673   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17674   도 트럼프 대통령 이날 크리스마스 연휴 앞두 세제 법안 서명 22 일 현지 시간 ...   
17675   나이스 피 앤 아이 최대 2019 년 건설 근로자 공제 회의 대체 투자 자문 되 ...   
17676   일각 신 회장 실형 받 경우 오너 부재 따르 악재 자금 조달 부정적 영향 끼치 수...   
17677   법원 빠르 시일 내 매각 내년 2 월 초 회생 계획안 하 계획 가지 것 전하 이번...   
17678   당초 연말 서명 늦추 수 있 전망 크리스마스 연휴 앞두 세제 개혁 마무리 미국인 ...   

                                             pos_article  
0       아시아 경제 박 나 영 기자 한국 예탁 결제 원 사장 1 일 신년 사 통하 전자 ...  
1       덕 훈 수출입 은행 장 머니 투데이 권 기자 신년 사 덕 훈 한국 수출입 은행 장...  
2       김 지 기자 금융 투자 업계 이번 주 2 6 일 국내 증시 화학 정보 기술 은행 ...  
3       이 데일리 이민 정 기자 1 일 현지 시간 터키 탄불 오르타 이 인근 나이트 클럽...  
4       코스 피 상단 밴드 2,150 2,350 전망

In [27]:
a = open('title_pos.txt','rb')
sum_title = pickle.load(a)
sum_title

pos_title  \
0                    예탁 결제 원 사장 전자 증권 제도 시행 기반 조성   
1                        덕 훈 행장 조선 등 취약 산업 연착륙 도모   
2                    화학 IT 등 경기 민 감주 주목 업 황 호조 기대   
3                         터키 나이트 클럽 총격 최소 35 명 사망   
4               정 유년 증시 힘차 울 라 대형 주 가격 떨어지 중소형 매력   
5                                 코스닥 1 월 효과 기대 주   
6                       채권 주식 유동성 대전환 2017 년 주식 해   
7                    스타 PB 6 부동산 채권 뭉칫돈 주식 원자재 유망   
8                   빚 테크 돈 벌 장기 대출 고정 1 년 내 변동 유리   
9                           커지 살 몸 집 키우 결전 벼르 증권업   
10                   2017 정유 업종 투자 기상도 반도체 맑 유통 림   
11                       정 유년 새둥지 트 삼성 대신 2 전성기 열   
12                   새해 박스 피 뚫 IT 에너지 산업 재 소재 유 망   
13                               1 월 효과 기대 중소형 펀드   
14                                         하이드 그룹   
15                      강 달러 유지 외국인 매수세 트럼프 취임 변수   
16               닭띠 CEO 광구 우리은행 장 민 영화 성공 후 행보 주목   
17                정 유년 거취 주목 붉 닭띠 CEO 조 용병 신한 은행장   
18                          명 퇴 애환 거리 간판 묘사 섬세 리얼   
19                    1 호 증권사 교보 김 대표 기업 가치 극대화 올   
20                     부럽 브라질 러시아 2016 주 통화 가치 날으   
21                                12 월 FOMC 사록 공개   
22                      글로벌 공략 가속화 세계 최고 수액 기업 도약   
23                  트럼프 행정부 출범 앞두 연초 변동성 심화 여부 주목   
24                 재계 정 유년 산 너머 산 위기 극복 DNA 도약 다짐   
25                    전인권 신대 철 아름 강산 촛불 승화 배신감 날리   
26               닭띠 CEO 광구 우리은행 장 민 영화 성공 후 행보 주목   
27                정 유년 거취 주목 붉 닭띠 CEO 조 용병 신한 은행장   
28                          명 퇴 애환 거리 간판 묘사 섬세 리얼   
29                    1 호 증권사 교보 김 대표 기업 가치 극대화 올   
...                                           ...   
17649                   2018 한국 경제 경제 통화 정책 내주 발표   
17650                       내년 중국 부동산 투자 급감 가능성 낮   
17651   다음주 코스 피 2420 2480 전망 27 일 경제 정책 방향 발표 주목   
17652                           크리스마스 연휴 앞두 소폭 하락   
17653             뉴욕 증시 성탄절 앞두 소폭 약세 우 0.11 하락 마감   
17654            뉴욕 증시 경제 지표 혼 조 속 소폭 하락 마감 우 0.1   
17655                  걸 근공 대체 투자 자문 사 나이스 피 앤 아이   
17656                 진 격의 롯데 칠성 음료 1 월 회사채 발행 개시   
17657                           건축 매각 공익 채무 낮추 진행   
17658           트럼프 세제 법안 서명 31 년 만 최대 감세 X 마스 선물   
17659                   2018 한국 경제 경제 통화 정책 내주 발표   
17660                       내년 중국 부동산 투자 급감 가능성 낮   
17661   다음주 코스 피 2420 2480 전망 27 일 경제 정책 방향 발표 주목   
17662                           크리스마스 연휴 앞두 소폭 하락   
17663             뉴욕 증시 성탄절 앞두 소폭 약세 우 0.11 하락 마감   
17664            뉴욕 증시 경제 지표 혼 조 속 소폭 하락 마감 우 0.1   
17665                  걸 근공 대체 투자 자문 사 나이스 피 앤 아이   
17666                 진 격의 롯데 칠성 음료 1 월 회사채 발행 개시   
17667                           건축 매각 공익 채무 낮추 진행   
17668           트럼프 세제 법안 서명 31 년 만 최대 감세 X 마스 선물   
17669                   2018 한국 경제 경제 통화 정책 내주 발표   
17670                       내년 중국 부동산 투자 급감 가능성 낮   
17671   다음주 코스 피 2420 2480 전망 27 일 경제 정책 방향 발표 주목   
17672                           크리스마스 연휴 앞두 소폭 하락   
17673             뉴욕 증시 성탄절 앞두 소폭 약세 우 0.11 하락 마감   
17674            뉴욕 증시 경제 지표 혼 조 속 소폭 하락 마감 우 0.1   
17675                  걸 근공 대체 투자 자문 사 나이스 피 앤 아이   
17676                 진 격의 롯데 칠성 음료 1 월 회사채 발행 개시   
17677                           건축 매각 공익 채무 낮추 진행   
17678           트럼프 세제 법안 서명 31 년 만 최대 감세 X 마스 선물   

                                      pos_title_origin  \
0                       이 예탁 결제 원 사장 전자 증권 제도 시행 기반 조성   
1                      이 덕 훈 행장 조선 등 취약 산업 연착륙 도모 하 어야   
2                         화학 IT 등 경기 민 감주 주목 업 황 호조 기대   
3                           터키 나이트 클럽 에서 총격 최소 35 명 사망   
4       정 유년 증시 힘차 게 울 어 라 대형 주 보다 는 가격 떨어지 ㄴ 중소형 주 매력   
5                                    코스닥 1 월 효과 기대 주 는   
6                          채권 주식 유동성 대전환 2017 년 주식 의 해   
7                    스타 PB 6 부동산 채권 뭉칫돈 주식 으로 원자재 도 유망   
8                빚 테크 로 돈 벌 기 장기 대출 은 고정 1 년 내 는 변동 유리   
9                    커지 어야 살 ㄴ다 몸 집 키우 고 결전 벼르 는 증권업 계   
10                2017 정유 년 업종 투자 기상도 는 반도체 맑 음 유통 흐 림   
11                 정 유년 새둥지 트 ㄴ 삼성 대신 저 의 2 의 전성기 열 ㄴ다   

In [15]:
yg_input = pd.concat([sum_input.pos_sum, sum_title.pos_title], axis=1)
yg_input

pos_sum  \
0       한국 예탁 결제 원 사장 1 일 신년 사 통하 전자 증권 제도 시행 기반 조성 라...   
1       교자 채신 힘 듣 가깝 곳 멀 곳 땔나무 캐 하 늘 의미 다이 행장 올해 과제 전...   
2       대신 증권 한솔 케미칼 최근 인수 자회사 팩스 이익 반영 수익성 강화 삼성전자 양...   
3       1 일 현지 시간 터키 탄불 오르타 이 인근 나이트 클럽 총격 사건 발생 최소 3...   
4       코스 피 상단 밴드 2150 2350 전망 2017 년 정유 증시 밝 주요 증권사...   
5       반도체 성수기 호재 자율 주행 차 등 성장주 유망 유니 동화 기업 평가 되 종목 ...   
6       따르 내년 삼성전자 추가 급등 국내 주요 기업 지주사 전환 잭 이벤트 예고 곽 현...   
7       김 팀장 중국 일대일 미국 인프라 투자 공약 감안 때 금속 중심 원자재 투자 유효...   
8       전문가 신규 장기 대출 받으 고정 금리 선택 기존 변동 금리 대출 받 고정 금리 ...   
9       8 조 원 이상 종합 금융 투자 계좌 개설 부동산 담보 신탁 업무 하 수 있 따르...   
10      임은 영 삼성 증권 연구원 중국 시장 소형차 구매 세 감면 연장 자동차 금융 비중...   
11      삼성 증권 서초 삼성 타운 이전 완료 강남 시대 자산 관리 역량 극대화 금융 계열...   
12      롯데 케미칼 부타디엔 체인 스프레드 확대 따르 이익 성장 전망 상장 조선사 중 재...   
13      양호 수익률 보이 가운데 브라질 주식 펀드 남미 신흥국 주식 펀드 51 315 오...   
14      해외 매출 비중 14 수준 베트남 중심 동남아 사료 시장 진출 하이드 그룹 어류 ...   
15      달러 강세 외국인 자금 국내 시장 이탈 것 김 성환 부국 증권 연구원 달러 부담 ...   
16      민 영화 성공 후 이 행장 개인적 우리 은행장 연임 새 시험대 앞 서 사외 이사 ...   
17      스마트 근무제 가 보수적 은행 조직 정착 수 있 회의적 시선 많 지난해 11 월 ...   
18      작품 시의 오 공동 당선작 정하 한편 수필 늘 성수 기와 비수기 재래시장 마트 차...   
19      더불 전문 사모 집합 투자업 사모 펀드 업 진출 다양 금융 상품 출시 고객 기반 ...   
20      나라 11 월 달러 부족 사태 통화 가치 48 절하 나이 지리 아 화 368 떨어...   
21      달러 향방 예측 위하 트럼프 재정 정책 연 주 금리 인상 시점 관 환 멘트 주시 ...   
22      세계 1 위 수액 기업 박스 터 생명 과학 영양 수액 기술 사 갈 정도 차 대표 ...   
23      트럼프 랠리 마침표 찍 데 트럼프 행정부 출범 앞두 도 트럼프 대통령 당선자 공약...   
24      현대 기아 차 그룹 올해 자율 주행 차 시대 등 대비 기술 개발 총력 기울이 미래...   
25      20161231 뉴스 1 저작권자 뉴스 1 코리 아 무단 전재 배포 금지 머니 투...   
26      민 영화 성공 후 이 행장 개인적 우리 은행장 연임 새 시험대 앞 서 사외 이사 ...   
27      스마트 근무제 가 보수적 은행 조직 정착 수 있 회의적 시선 많 지난해 11 월 ...   
28      작품 시의 오 공동 당선작 정하 한편 수필 늘 성수 기와 비수기 재래시장 마트 차...   
29      더불 전문 사모 집합 투자업 사모 펀드 업 진출 다양 금융 상품 출시 고객 기반 ...   
...                                                  ...   
17649   지난달 말 기준 금리 인상 기대 시장 금리 상승 점 대출 금리 반영 것 보이 27...   
17650   질적 성장 무게 감 두 방침 하 최 연구원 중국 정부 2020 년 금융 리스크 통...   
17651   투자 증권 다음주 올해 마지막 거래 주간 코스 피 밴드 2420 2480 전망 내...   
17652   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17653   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17654   도 트럼프 대통령 이날 크리스마스 연휴 앞두 세제 법안 서명 22 일 현지 시간 ...   
17655   나이스 피 앤 아이 최대 2019 년 건설 근로자 공제 회의 대체 투자 자문 되 ...   
17656   일각 신 회장 실형 받 경우 오너 부재 따르 악재 자금 조달 부정적 영향 끼치 수...   
17657   법원 빠르 시일 내 매각 내년 2 월 초 회생 계획안 하 계획 가지 것 전하 이번...   
17658   당초 연말 서명 늦추 수 있 전망 크리스마스 연휴 앞두 세제 개혁 마무리 미국인 ...   
17659   지난달 말 기준 금리 인상 기대 시장 금리 상승 점 대출 금리 반영 것 보이 27...   
17660   질적 성장 무게 감 두 방침 하 최 연구원 중국 정부 2020 년 금융 리스크 통...   
17661   투자 증권 다음주 올해 마지막 거래 주간 코스 피 밴드 2420 2480 전망 내...   
17662   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17663   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17664   도 트럼프 대통령 이날 크리스마스 연휴 앞두 세제 법안 서명 22 일 현지 시간 ...   
17665   나이스 피 앤 아이 최대 2019 년 건설 근로자 공제 회의 대체 투자 자문 되 ...   
17666   일각 신 회장 실형 받 경우 오너 부재 따르 악재 자금 조달 부정적 영향 끼치 수...   
17667   법원 빠르 시일 내 매각 내년 2 월 초 회생 계획안 하 계획 가지 것 전하 이번...   
17668   당초 연말 서명 늦추 수 있 전망 크리스마스 연휴 앞두 세제 개혁 마무리 미국인 ...   
17669   지난달 말 기준 금리 인상 기대 시장 금리 상승 점 대출 금리 반영 것 보이 27...   
17670   질적 성장 무게 감 두 방침 하 최 연구원 중국 정부 2020 년 금융 리스크 통...   
17671   배당 수익률 상위 종목 산 46 메 리 종 금 증권 46 기업 은행 44 효성 4...   
17672   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17673   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17674   도 트럼프 대통령 이날 크리스마스 연휴 앞두 세제 법안 서명 22 일 현지 시간 ...   
17675   나이스 피 앤 아이 최대 2019 년 건설 근로자 공제 회의 대체 투자 자문 되 ...   
17676   일각 신 회장 실형 받 경우 오너 부재 따르 악재 자금 조달 부정적 영향 끼치 수...   
17677   법원 빠르 시일 내 매각 내년 2 월 초 회생 계획안 하 계획 가지 것 전하 이번...   
17678   당초 연말 서명 늦추 수 있 전망 크리스마스 연휴 앞두 세제 개혁 마무리 미국인 ...   

                                        pos_title  
0                    예탁 결제 원 사장 전자 증권 제도 시행 기반 조성  
1                        덕 훈 행장 조선 등 취약 산업 연착륙 도모  
2                    화학 IT 등 경기 민 감주 주목 업 황 호조 기대  
3                         터키 나이트 클럽 총격 최소 35 명 사망  
4               정 유년 증시 힘차 울 라 대형 주 가격 떨어지 중소형 매력  
5               

In [29]:
sb_input = pd.concat([sum_title.pos_title, sum_title.pos_title_origin], axis=1)
sb_input

pos_title  \
0                    예탁 결제 원 사장 전자 증권 제도 시행 기반 조성   
1                        덕 훈 행장 조선 등 취약 산업 연착륙 도모   
2                    화학 IT 등 경기 민 감주 주목 업 황 호조 기대   
3                         터키 나이트 클럽 총격 최소 35 명 사망   
4               정 유년 증시 힘차 울 라 대형 주 가격 떨어지 중소형 매력   
5                                 코스닥 1 월 효과 기대 주   
6                       채권 주식 유동성 대전환 2017 년 주식 해   
7                    스타 PB 6 부동산 채권 뭉칫돈 주식 원자재 유망   
8                   빚 테크 돈 벌 장기 대출 고정 1 년 내 변동 유리   
9                           커지 살 몸 집 키우 결전 벼르 증권업   
10                   2017 정유 업종 투자 기상도 반도체 맑 유통 림   
11                       정 유년 새둥지 트 삼성 대신 2 전성기 열   
12                   새해 박스 피 뚫 IT 에너지 산업 재 소재 유 망   
13                               1 월 효과 기대 중소형 펀드   
14                                         하이드 그룹   
15                      강 달러 유지 외국인 매수세 트럼프 취임 변수   
16               닭띠 CEO 광구 우리은행 장 민 영화 성공 후 행보 주목   
17                정 유년 거취 주목 붉 닭띠 CEO 조 용병 신한 은행장   
18                          명 퇴 애환 거리 간판 묘사 섬세 리얼   
19                    1 호 증권사 교보 김 대표 기업 가치 극대화 올   
20                     부럽 브라질 러시아 2016 주 통화 가치 날으   
21                                12 월 FOMC 사록 공개   
22                      글로벌 공략 가속화 세계 최고 수액 기업 도약   
23                  트럼프 행정부 출범 앞두 연초 변동성 심화 여부 주목   
24                 재계 정 유년 산 너머 산 위기 극복 DNA 도약 다짐   
25                    전인권 신대 철 아름 강산 촛불 승화 배신감 날리   
26               닭띠 CEO 광구 우리은행 장 민 영화 성공 후 행보 주목   
27                정 유년 거취 주목 붉 닭띠 CEO 조 용병 신한 은행장   
28                          명 퇴 애환 거리 간판 묘사 섬세 리얼   
29                    1 호 증권사 교보 김 대표 기업 가치 극대화 올   
...                                           ...   
17649                   2018 한국 경제 경제 통화 정책 내주 발표   
17650                       내년 중국 부동산 투자 급감 가능성 낮   
17651   다음주 코스 피 2420 2480 전망 27 일 경제 정책 방향 발표 주목   
17652                           크리스마스 연휴 앞두 소폭 하락   
17653             뉴욕 증시 성탄절 앞두 소폭 약세 우 0.11 하락 마감   
17654            뉴욕 증시 경제 지표 혼 조 속 소폭 하락 마감 우 0.1   
17655                  걸 근공 대체 투자 자문 사 나이스 피 앤 아이   
17656                 진 격의 롯데 칠성 음료 1 월 회사채 발행 개시   
17657                           건축 매각 공익 채무 낮추 진행   
17658           트럼프 세제 법안 서명 31 년 만 최대 감세 X 마스 선물   
17659                   2018 한국 경제 경제 통화 정책 내주 발표   
17660                       내년 중국 부동산 투자 급감 가능성 낮   
17661   다음주 코스 피 2420 2480 전망 27 일 경제 정책 방향 발표 주목   
17662                           크리스마스 연휴 앞두 소폭 하락   
17663             뉴욕 증시 성탄절 앞두 소폭 약세 우 0.11 하락 마감   
17664            뉴욕 증시 경제 지표 혼 조 속 소폭 하락 마감 우 0.1   
17665                  걸 근공 대체 투자 자문 사 나이스 피 앤 아이   
17666                 진 격의 롯데 칠성 음료 1 월 회사채 발행 개시   
17667                           건축 매각 공익 채무 낮추 진행   
17668           트럼프 세제 법안 서명 31 년 만 최대 감세 X 마스 선물   
17669                   2018 한국 경제 경제 통화 정책 내주 발표   
17670                       내년 중국 부동산 투자 급감 가능성 낮   
17671   다음주 코스 피 2420 2480 전망 27 일 경제 정책 방향 발표 주목   
17672                           크리스마스 연휴 앞두 소폭 하락   
17673             뉴욕 증시 성탄절 앞두 소폭 약세 우 0.11 하락 마감   
17674            뉴욕 증시 경제 지표 혼 조 속 소폭 하락 마감 우 0.1   
17675                  걸 근공 대체 투자 자문 사 나이스 피 앤 아이   
17676                 진 격의 롯데 칠성 음료 1 월 회사채 발행 개시   
17677                           건축 매각 공익 채무 낮추 진행   
17678           트럼프 세제 법안 서명 31 년 만 최대 감세 X 마스 선물   

                                      pos_title_origin  
0                       이 예탁 결제 원 사장 전자 증권 제도 시행 기반 조성  
1                      이 덕 훈 행장 조선 등 취약 산업 연착륙 도모 하 어야  
2                         화학 IT 등 경기 민 감주 주목 업 황 호조 기대  
3                           터키 나이트 클럽 에서 총격 최소 35 명 사망  
4       정 유년 증시 힘차 게 울 어 라 대형 주 보다 는 가격 떨어지 ㄴ 중소형 주 매력  
5                                    코스닥 1 월 효과 기대 주 는  
6                          채권 주식 유동성 대전환 2017 년 주식 의 해  
7                    스타 PB 6 부동산 채권 뭉칫돈 주식 으로 원자재 도 유망  
8                빚 테크 로 돈 벌 기 장기 대출 은 고정 1 년 내 는 변동 유리  
9                    커지 어야 살 ㄴ다 몸 집 키우 고 결전 벼르 는 증권업 계  
10                2017 정유 년 업종 투자 기상도 는 반도체 맑 음 유통 흐 림  
11                 정 유년 새둥지 트 ㄴ 삼성 대신 저 의 2 의 전성기 열 ㄴ다  
12          

In [16]:
f = open('yg_input.txt', 'wb')
pickle.dump(yg_input, f)
f.close()

In [30]:
f = open('sb_input.txt', 'wb')
pickle.dump(sb_input, f)
f.close()

In [18]:
a = open('yg_input.txt','rb')
pickle.load(a)

pos_sum  \
0       한국 예탁 결제 원 사장 1 일 신년 사 통하 전자 증권 제도 시행 기반 조성 라...   
1       교자 채신 힘 듣 가깝 곳 멀 곳 땔나무 캐 하 늘 의미 다이 행장 올해 과제 전...   
2       대신 증권 한솔 케미칼 최근 인수 자회사 팩스 이익 반영 수익성 강화 삼성전자 양...   
3       1 일 현지 시간 터키 탄불 오르타 이 인근 나이트 클럽 총격 사건 발생 최소 3...   
4       코스 피 상단 밴드 2150 2350 전망 2017 년 정유 증시 밝 주요 증권사...   
5       반도체 성수기 호재 자율 주행 차 등 성장주 유망 유니 동화 기업 평가 되 종목 ...   
6       따르 내년 삼성전자 추가 급등 국내 주요 기업 지주사 전환 잭 이벤트 예고 곽 현...   
7       김 팀장 중국 일대일 미국 인프라 투자 공약 감안 때 금속 중심 원자재 투자 유효...   
8       전문가 신규 장기 대출 받으 고정 금리 선택 기존 변동 금리 대출 받 고정 금리 ...   
9       8 조 원 이상 종합 금융 투자 계좌 개설 부동산 담보 신탁 업무 하 수 있 따르...   
10      임은 영 삼성 증권 연구원 중국 시장 소형차 구매 세 감면 연장 자동차 금융 비중...   
11      삼성 증권 서초 삼성 타운 이전 완료 강남 시대 자산 관리 역량 극대화 금융 계열...   
12      롯데 케미칼 부타디엔 체인 스프레드 확대 따르 이익 성장 전망 상장 조선사 중 재...   
13      양호 수익률 보이 가운데 브라질 주식 펀드 남미 신흥국 주식 펀드 51 315 오...   
14      해외 매출 비중 14 수준 베트남 중심 동남아 사료 시장 진출 하이드 그룹 어류 ...   
15      달러 강세 외국인 자금 국내 시장 이탈 것 김 성환 부국 증권 연구원 달러 부담 ...   
16      민 영화 성공 후 이 행장 개인적 우리 은행장 연임 새 시험대 앞 서 사외 이사 ...   
17      스마트 근무제 가 보수적 은행 조직 정착 수 있 회의적 시선 많 지난해 11 월 ...   
18      작품 시의 오 공동 당선작 정하 한편 수필 늘 성수 기와 비수기 재래시장 마트 차...   
19      더불 전문 사모 집합 투자업 사모 펀드 업 진출 다양 금융 상품 출시 고객 기반 ...   
20      나라 11 월 달러 부족 사태 통화 가치 48 절하 나이 지리 아 화 368 떨어...   
21      달러 향방 예측 위하 트럼프 재정 정책 연 주 금리 인상 시점 관 환 멘트 주시 ...   
22      세계 1 위 수액 기업 박스 터 생명 과학 영양 수액 기술 사 갈 정도 차 대표 ...   
23      트럼프 랠리 마침표 찍 데 트럼프 행정부 출범 앞두 도 트럼프 대통령 당선자 공약...   
24      현대 기아 차 그룹 올해 자율 주행 차 시대 등 대비 기술 개발 총력 기울이 미래...   
25      20161231 뉴스 1 저작권자 뉴스 1 코리 아 무단 전재 배포 금지 머니 투...   
26      민 영화 성공 후 이 행장 개인적 우리 은행장 연임 새 시험대 앞 서 사외 이사 ...   
27      스마트 근무제 가 보수적 은행 조직 정착 수 있 회의적 시선 많 지난해 11 월 ...   
28      작품 시의 오 공동 당선작 정하 한편 수필 늘 성수 기와 비수기 재래시장 마트 차...   
29      더불 전문 사모 집합 투자업 사모 펀드 업 진출 다양 금융 상품 출시 고객 기반 ...   
...                                                  ...   
17649   지난달 말 기준 금리 인상 기대 시장 금리 상승 점 대출 금리 반영 것 보이 27...   
17650   질적 성장 무게 감 두 방침 하 최 연구원 중국 정부 2020 년 금융 리스크 통...   
17651   투자 증권 다음주 올해 마지막 거래 주간 코스 피 밴드 2420 2480 전망 내...   
17652   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17653   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17654   도 트럼프 대통령 이날 크리스마스 연휴 앞두 세제 법안 서명 22 일 현지 시간 ...   
17655   나이스 피 앤 아이 최대 2019 년 건설 근로자 공제 회의 대체 투자 자문 되 ...   
17656   일각 신 회장 실형 받 경우 오너 부재 따르 악재 자금 조달 부정적 영향 끼치 수...   
17657   법원 빠르 시일 내 매각 내년 2 월 초 회생 계획안 하 계획 가지 것 전하 이번...   
17658   당초 연말 서명 늦추 수 있 전망 크리스마스 연휴 앞두 세제 개혁 마무리 미국인 ...   
17659   지난달 말 기준 금리 인상 기대 시장 금리 상승 점 대출 금리 반영 것 보이 27...   
17660   질적 성장 무게 감 두 방침 하 최 연구원 중국 정부 2020 년 금융 리스크 통...   
17661   투자 증권 다음주 올해 마지막 거래 주간 코스 피 밴드 2420 2480 전망 내...   
17662   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17663   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17664   도 트럼프 대통령 이날 크리스마스 연휴 앞두 세제 법안 서명 22 일 현지 시간 ...   
17665   나이스 피 앤 아이 최대 2019 년 건설 근로자 공제 회의 대체 투자 자문 되 ...   
17666   일각 신 회장 실형 받 경우 오너 부재 따르 악재 자금 조달 부정적 영향 끼치 수...   
17667   법원 빠르 시일 내 매각 내년 2 월 초 회생 계획안 하 계획 가지 것 전하 이번...   
17668   당초 연말 서명 늦추 수 있 전망 크리스마스 연휴 앞두 세제 개혁 마무리 미국인 ...   
17669   지난달 말 기준 금리 인상 기대 시장 금리 상승 점 대출 금리 반영 것 보이 27...   
17670   질적 성장 무게 감 두 방침 하 최 연구원 중국 정부 2020 년 금융 리스크 통...   
17671   배당 수익률 상위 종목 산 46 메 리 종 금 증권 46 기업 은행 44 효성 4...   
17672   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17673   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17674   도 트럼프 대통령 이날 크리스마스 연휴 앞두 세제 법안 서명 22 일 현지 시간 ...   
17675   나이스 피 앤 아이 최대 2019 년 건설 근로자 공제 회의 대체 투자 자문 되 ...   
17676   일각 신 회장 실형 받 경우 오너 부재 따르 악재 자금 조달 부정적 영향 끼치 수...   
17677   법원 빠르 시일 내 매각 내년 2 월 초 회생 계획안 하 계획 가지 것 전하 이번...   
17678   당초 연말 서명 늦추 수 있 전망 크리스마스 연휴 앞두 세제 개혁 마무리 미국인 ...   

                                        pos_title  
0                    예탁 결제 원 사장 전자 증권 제도 시행 기반 조성  
1                        덕 훈 행장 조선 등 취약 산업 연착륙 도모  
2                    화학 IT 등 경기 민 감주 주목 업 황 호조 기대  
3                         터키 나이트 클럽 총격 최소 35 명 사망  
4               정 유년 증시 힘차 울 라 대형 주 가격 떨어지 중소형 매력  
5               

In [31]:
a = open('sb_input.txt','rb')
pickle.load(a)

pos_title  \
0                    예탁 결제 원 사장 전자 증권 제도 시행 기반 조성   
1                        덕 훈 행장 조선 등 취약 산업 연착륙 도모   
2                    화학 IT 등 경기 민 감주 주목 업 황 호조 기대   
3                         터키 나이트 클럽 총격 최소 35 명 사망   
4               정 유년 증시 힘차 울 라 대형 주 가격 떨어지 중소형 매력   
5                                 코스닥 1 월 효과 기대 주   
6                       채권 주식 유동성 대전환 2017 년 주식 해   
7                    스타 PB 6 부동산 채권 뭉칫돈 주식 원자재 유망   
8                   빚 테크 돈 벌 장기 대출 고정 1 년 내 변동 유리   
9                           커지 살 몸 집 키우 결전 벼르 증권업   
10                   2017 정유 업종 투자 기상도 반도체 맑 유통 림   
11                       정 유년 새둥지 트 삼성 대신 2 전성기 열   
12                   새해 박스 피 뚫 IT 에너지 산업 재 소재 유 망   
13                               1 월 효과 기대 중소형 펀드   
14                                         하이드 그룹   
15                      강 달러 유지 외국인 매수세 트럼프 취임 변수   
16               닭띠 CEO 광구 우리은행 장 민 영화 성공 후 행보 주목   
17                정 유년 거취 주목 붉 닭띠 CEO 조 용병 신한 은행장   
18                          명 퇴 애환 거리 간판 묘사 섬세 리얼   
19                    1 호 증권사 교보 김 대표 기업 가치 극대화 올   
20                     부럽 브라질 러시아 2016 주 통화 가치 날으   
21                                12 월 FOMC 사록 공개   
22                      글로벌 공략 가속화 세계 최고 수액 기업 도약   
23                  트럼프 행정부 출범 앞두 연초 변동성 심화 여부 주목   
24                 재계 정 유년 산 너머 산 위기 극복 DNA 도약 다짐   
25                    전인권 신대 철 아름 강산 촛불 승화 배신감 날리   
26               닭띠 CEO 광구 우리은행 장 민 영화 성공 후 행보 주목   
27                정 유년 거취 주목 붉 닭띠 CEO 조 용병 신한 은행장   
28                          명 퇴 애환 거리 간판 묘사 섬세 리얼   
29                    1 호 증권사 교보 김 대표 기업 가치 극대화 올   
...                                           ...   
17649                   2018 한국 경제 경제 통화 정책 내주 발표   
17650                       내년 중국 부동산 투자 급감 가능성 낮   
17651   다음주 코스 피 2420 2480 전망 27 일 경제 정책 방향 발표 주목   
17652                           크리스마스 연휴 앞두 소폭 하락   
17653             뉴욕 증시 성탄절 앞두 소폭 약세 우 0.11 하락 마감   
17654            뉴욕 증시 경제 지표 혼 조 속 소폭 하락 마감 우 0.1   
17655                  걸 근공 대체 투자 자문 사 나이스 피 앤 아이   
17656                 진 격의 롯데 칠성 음료 1 월 회사채 발행 개시   
17657                           건축 매각 공익 채무 낮추 진행   
17658           트럼프 세제 법안 서명 31 년 만 최대 감세 X 마스 선물   
17659                   2018 한국 경제 경제 통화 정책 내주 발표   
17660                       내년 중국 부동산 투자 급감 가능성 낮   
17661   다음주 코스 피 2420 2480 전망 27 일 경제 정책 방향 발표 주목   
17662                           크리스마스 연휴 앞두 소폭 하락   
17663             뉴욕 증시 성탄절 앞두 소폭 약세 우 0.11 하락 마감   
17664            뉴욕 증시 경제 지표 혼 조 속 소폭 하락 마감 우 0.1   
17665                  걸 근공 대체 투자 자문 사 나이스 피 앤 아이   
17666                 진 격의 롯데 칠성 음료 1 월 회사채 발행 개시   
17667                           건축 매각 공익 채무 낮추 진행   
17668           트럼프 세제 법안 서명 31 년 만 최대 감세 X 마스 선물   
17669                   2018 한국 경제 경제 통화 정책 내주 발표   
17670                       내년 중국 부동산 투자 급감 가능성 낮   
17671   다음주 코스 피 2420 2480 전망 27 일 경제 정책 방향 발표 주목   
17672                           크리스마스 연휴 앞두 소폭 하락   
17673             뉴욕 증시 성탄절 앞두 소폭 약세 우 0.11 하락 마감   
17674            뉴욕 증시 경제 지표 혼 조 속 소폭 하락 마감 우 0.1   
17675                  걸 근공 대체 투자 자문 사 나이스 피 앤 아이   
17676                 진 격의 롯데 칠성 음료 1 월 회사채 발행 개시   
17677                           건축 매각 공익 채무 낮추 진행   
17678           트럼프 세제 법안 서명 31 년 만 최대 감세 X 마스 선물   

                                      pos_title_origin  
0                       이 예탁 결제 원 사장 전자 증권 제도 시행 기반 조성  
1                      이 덕 훈 행장 조선 등 취약 산업 연착륙 도모 하 어야  
2                         화학 IT 등 경기 민 감주 주목 업 황 호조 기대  
3                           터키 나이트 클럽 에서 총격 최소 35 명 사망  
4       정 유년 증시 힘차 게 울 어 라 대형 주 보다 는 가격 떨어지 ㄴ 중소형 주 매력  
5                                    코스닥 1 월 효과 기대 주 는  
6                          채권 주식 유동성 대전환 2017 년 주식 의 해  
7                    스타 PB 6 부동산 채권 뭉칫돈 주식 으로 원자재 도 유망  
8                빚 테크 로 돈 벌 기 장기 대출 은 고정 1 년 내 는 변동 유리  
9                    커지 어야 살 ㄴ다 몸 집 키우 고 결전 벼르 는 증권업 계  
10                2017 정유 년 업종 투자 기상도 는 반도체 맑 음 유통 흐 림  
11                 정 유년 새둥지 트 ㄴ 삼성 대신 저 의 2 의 전성기 열 ㄴ다  
12          

In [20]:
yg_input.to_csv('yg_input.csv', index=False)

In [32]:
sb_input.to_csv('sb_input.csv', index=False)

In [22]:
pd.read_csv('yg_input.csv', encoding="cp949")

pos_sum  \
0       한국 예탁 결제 원 사장 1 일 신년 사 통하 전자 증권 제도 시행 기반 조성 라...   
1       교자 채신 힘 듣 가깝 곳 멀 곳 땔나무 캐 하 늘 의미 다이 행장 올해 과제 전...   
2       대신 증권 한솔 케미칼 최근 인수 자회사 팩스 이익 반영 수익성 강화 삼성전자 양...   
3       1 일 현지 시간 터키 탄불 오르타 이 인근 나이트 클럽 총격 사건 발생 최소 3...   
4       코스 피 상단 밴드 2150 2350 전망 2017 년 정유 증시 밝 주요 증권사...   
5       반도체 성수기 호재 자율 주행 차 등 성장주 유망 유니 동화 기업 평가 되 종목 ...   
6       따르 내년 삼성전자 추가 급등 국내 주요 기업 지주사 전환 잭 이벤트 예고 곽 현...   
7       김 팀장 중국 일대일 미국 인프라 투자 공약 감안 때 금속 중심 원자재 투자 유효...   
8       전문가 신규 장기 대출 받으 고정 금리 선택 기존 변동 금리 대출 받 고정 금리 ...   
9       8 조 원 이상 종합 금융 투자 계좌 개설 부동산 담보 신탁 업무 하 수 있 따르...   
10      임은 영 삼성 증권 연구원 중국 시장 소형차 구매 세 감면 연장 자동차 금융 비중...   
11      삼성 증권 서초 삼성 타운 이전 완료 강남 시대 자산 관리 역량 극대화 금융 계열...   
12      롯데 케미칼 부타디엔 체인 스프레드 확대 따르 이익 성장 전망 상장 조선사 중 재...   
13      양호 수익률 보이 가운데 브라질 주식 펀드 남미 신흥국 주식 펀드 51 315 오...   
14      해외 매출 비중 14 수준 베트남 중심 동남아 사료 시장 진출 하이드 그룹 어류 ...   
15      달러 강세 외국인 자금 국내 시장 이탈 것 김 성환 부국 증권 연구원 달러 부담 ...   
16      민 영화 성공 후 이 행장 개인적 우리 은행장 연임 새 시험대 앞 서 사외 이사 ...   
17      스마트 근무제 가 보수적 은행 조직 정착 수 있 회의적 시선 많 지난해 11 월 ...   
18      작품 시의 오 공동 당선작 정하 한편 수필 늘 성수 기와 비수기 재래시장 마트 차...   
19      더불 전문 사모 집합 투자업 사모 펀드 업 진출 다양 금융 상품 출시 고객 기반 ...   
20      나라 11 월 달러 부족 사태 통화 가치 48 절하 나이 지리 아 화 368 떨어...   
21      달러 향방 예측 위하 트럼프 재정 정책 연 주 금리 인상 시점 관 환 멘트 주시 ...   
22      세계 1 위 수액 기업 박스 터 생명 과학 영양 수액 기술 사 갈 정도 차 대표 ...   
23      트럼프 랠리 마침표 찍 데 트럼프 행정부 출범 앞두 도 트럼프 대통령 당선자 공약...   
24      현대 기아 차 그룹 올해 자율 주행 차 시대 등 대비 기술 개발 총력 기울이 미래...   
25      20161231 뉴스 1 저작권자 뉴스 1 코리 아 무단 전재 배포 금지 머니 투...   
26      민 영화 성공 후 이 행장 개인적 우리 은행장 연임 새 시험대 앞 서 사외 이사 ...   
27      스마트 근무제 가 보수적 은행 조직 정착 수 있 회의적 시선 많 지난해 11 월 ...   
28      작품 시의 오 공동 당선작 정하 한편 수필 늘 성수 기와 비수기 재래시장 마트 차...   
29      더불 전문 사모 집합 투자업 사모 펀드 업 진출 다양 금융 상품 출시 고객 기반 ...   
...                                                  ...   
17649   지난달 말 기준 금리 인상 기대 시장 금리 상승 점 대출 금리 반영 것 보이 27...   
17650   질적 성장 무게 감 두 방침 하 최 연구원 중국 정부 2020 년 금융 리스크 통...   
17651   투자 증권 다음주 올해 마지막 거래 주간 코스 피 밴드 2420 2480 전망 내...   
17652   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17653   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17654   도 트럼프 대통령 이날 크리스마스 연휴 앞두 세제 법안 서명 22 일 현지 시간 ...   
17655   나이스 피 앤 아이 최대 2019 년 건설 근로자 공제 회의 대체 투자 자문 되 ...   
17656   일각 신 회장 실형 받 경우 오너 부재 따르 악재 자금 조달 부정적 영향 끼치 수...   
17657   법원 빠르 시일 내 매각 내년 2 월 초 회생 계획안 하 계획 가지 것 전하 이번...   
17658   당초 연말 서명 늦추 수 있 전망 크리스마스 연휴 앞두 세제 개혁 마무리 미국인 ...   
17659   지난달 말 기준 금리 인상 기대 시장 금리 상승 점 대출 금리 반영 것 보이 27...   
17660   질적 성장 무게 감 두 방침 하 최 연구원 중국 정부 2020 년 금융 리스크 통...   
17661   투자 증권 다음주 올해 마지막 거래 주간 코스 피 밴드 2420 2480 전망 내...   
17662   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17663   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17664   도 트럼프 대통령 이날 크리스마스 연휴 앞두 세제 법안 서명 22 일 현지 시간 ...   
17665   나이스 피 앤 아이 최대 2019 년 건설 근로자 공제 회의 대체 투자 자문 되 ...   
17666   일각 신 회장 실형 받 경우 오너 부재 따르 악재 자금 조달 부정적 영향 끼치 수...   
17667   법원 빠르 시일 내 매각 내년 2 월 초 회생 계획안 하 계획 가지 것 전하 이번...   
17668   당초 연말 서명 늦추 수 있 전망 크리스마스 연휴 앞두 세제 개혁 마무리 미국인 ...   
17669   지난달 말 기준 금리 인상 기대 시장 금리 상승 점 대출 금리 반영 것 보이 27...   
17670   질적 성장 무게 감 두 방침 하 최 연구원 중국 정부 2020 년 금융 리스크 통...   
17671   배당 수익률 상위 종목 산 46 메 리 종 금 증권 46 기업 은행 44 효성 4...   
17672   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17673   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17674   도 트럼프 대통령 이날 크리스마스 연휴 앞두 세제 법안 서명 22 일 현지 시간 ...   
17675   나이스 피 앤 아이 최대 2019 년 건설 근로자 공제 회의 대체 투자 자문 되 ...   
17676   일각 신 회장 실형 받 경우 오너 부재 따르 악재 자금 조달 부정적 영향 끼치 수...   
17677   법원 빠르 시일 내 매각 내년 2 월 초 회생 계획안 하 계획 가지 것 전하 이번...   
17678   당초 연말 서명 늦추 수 있 전망 크리스마스 연휴 앞두 세제 개혁 마무리 미국인 ...   

                                        pos_title  
0                    예탁 결제 원 사장 전자 증권 제도 시행 기반 조성  
1                        덕 훈 행장 조선 등 취약 산업 연착륙 도모  
2                    화학 IT 등 경기 민 감주 주목 업 황 호조 기대  
3                         터키 나이트 클럽 총격 최소 35 명 사망  
4               정 유년 증시 힘차 울 라 대형 주 가격 떨어지 중소형 매력  
5               

In [33]:
pd.read_csv('sb_input.csv', encoding="cp949")

pos_title  \
0                    예탁 결제 원 사장 전자 증권 제도 시행 기반 조성   
1                        덕 훈 행장 조선 등 취약 산업 연착륙 도모   
2                    화학 IT 등 경기 민 감주 주목 업 황 호조 기대   
3                         터키 나이트 클럽 총격 최소 35 명 사망   
4               정 유년 증시 힘차 울 라 대형 주 가격 떨어지 중소형 매력   
5                                 코스닥 1 월 효과 기대 주   
6                       채권 주식 유동성 대전환 2017 년 주식 해   
7                    스타 PB 6 부동산 채권 뭉칫돈 주식 원자재 유망   
8                   빚 테크 돈 벌 장기 대출 고정 1 년 내 변동 유리   
9                           커지 살 몸 집 키우 결전 벼르 증권업   
10                   2017 정유 업종 투자 기상도 반도체 맑 유통 림   
11                       정 유년 새둥지 트 삼성 대신 2 전성기 열   
12                   새해 박스 피 뚫 IT 에너지 산업 재 소재 유 망   
13                               1 월 효과 기대 중소형 펀드   
14                                         하이드 그룹   
15                      강 달러 유지 외국인 매수세 트럼프 취임 변수   
16               닭띠 CEO 광구 우리은행 장 민 영화 성공 후 행보 주목   
17                정 유년 거취 주목 붉 닭띠 CEO 조 용병 신한 은행장   
18                          명 퇴 애환 거리 간판 묘사 섬세 리얼   
19                    1 호 증권사 교보 김 대표 기업 가치 극대화 올   
20                     부럽 브라질 러시아 2016 주 통화 가치 날으   
21                                12 월 FOMC 사록 공개   
22                      글로벌 공략 가속화 세계 최고 수액 기업 도약   
23                  트럼프 행정부 출범 앞두 연초 변동성 심화 여부 주목   
24                 재계 정 유년 산 너머 산 위기 극복 DNA 도약 다짐   
25                    전인권 신대 철 아름 강산 촛불 승화 배신감 날리   
26               닭띠 CEO 광구 우리은행 장 민 영화 성공 후 행보 주목   
27                정 유년 거취 주목 붉 닭띠 CEO 조 용병 신한 은행장   
28                          명 퇴 애환 거리 간판 묘사 섬세 리얼   
29                    1 호 증권사 교보 김 대표 기업 가치 극대화 올   
...                                           ...   
17649                   2018 한국 경제 경제 통화 정책 내주 발표   
17650                       내년 중국 부동산 투자 급감 가능성 낮   
17651   다음주 코스 피 2420 2480 전망 27 일 경제 정책 방향 발표 주목   
17652                           크리스마스 연휴 앞두 소폭 하락   
17653             뉴욕 증시 성탄절 앞두 소폭 약세 우 0.11 하락 마감   
17654            뉴욕 증시 경제 지표 혼 조 속 소폭 하락 마감 우 0.1   
17655                  걸 근공 대체 투자 자문 사 나이스 피 앤 아이   
17656                 진 격의 롯데 칠성 음료 1 월 회사채 발행 개시   
17657                           건축 매각 공익 채무 낮추 진행   
17658           트럼프 세제 법안 서명 31 년 만 최대 감세 X 마스 선물   
17659                   2018 한국 경제 경제 통화 정책 내주 발표   
17660                       내년 중국 부동산 투자 급감 가능성 낮   
17661   다음주 코스 피 2420 2480 전망 27 일 경제 정책 방향 발표 주목   
17662                           크리스마스 연휴 앞두 소폭 하락   
17663             뉴욕 증시 성탄절 앞두 소폭 약세 우 0.11 하락 마감   
17664            뉴욕 증시 경제 지표 혼 조 속 소폭 하락 마감 우 0.1   
17665                  걸 근공 대체 투자 자문 사 나이스 피 앤 아이   
17666                 진 격의 롯데 칠성 음료 1 월 회사채 발행 개시   
17667                           건축 매각 공익 채무 낮추 진행   
17668           트럼프 세제 법안 서명 31 년 만 최대 감세 X 마스 선물   
17669                   2018 한국 경제 경제 통화 정책 내주 발표   
17670                       내년 중국 부동산 투자 급감 가능성 낮   
17671   다음주 코스 피 2420 2480 전망 27 일 경제 정책 방향 발표 주목   
17672                           크리스마스 연휴 앞두 소폭 하락   
17673             뉴욕 증시 성탄절 앞두 소폭 약세 우 0.11 하락 마감   
17674            뉴욕 증시 경제 지표 혼 조 속 소폭 하락 마감 우 0.1   
17675                  걸 근공 대체 투자 자문 사 나이스 피 앤 아이   
17676                 진 격의 롯데 칠성 음료 1 월 회사채 발행 개시   
17677                           건축 매각 공익 채무 낮추 진행   
17678           트럼프 세제 법안 서명 31 년 만 최대 감세 X 마스 선물   

                                      pos_title_origin  
0                       이 예탁 결제 원 사장 전자 증권 제도 시행 기반 조성  
1                      이 덕 훈 행장 조선 등 취약 산업 연착륙 도모 하 어야  
2                         화학 IT 등 경기 민 감주 주목 업 황 호조 기대  
3                           터키 나이트 클럽 에서 총격 최소 35 명 사망  
4       정 유년 증시 힘차 게 울 어 라 대형 주 보다 는 가격 떨어지 ㄴ 중소형 주 매력  
5                                    코스닥 1 월 효과 기대 주 는  
6                          채권 주식 유동성 대전환 2017 년 주식 의 해  
7                    스타 PB 6 부동산 채권 뭉칫돈 주식 으로 원자재 도 유망  
8                빚 테크 로 돈 벌 기 장기 대출 은 고정 1 년 내 는 변동 유리  
9                    커지 어야 살 ㄴ다 몸 집 키우 고 결전 벼르 는 증권업 계  
10                2017 정유 년 업종 투자 기상도 는 반도체 맑 음 유통 흐 림  
11                 정 유년 새둥지 트 ㄴ 삼성 대신 저 의 2 의 전성기 열 ㄴ다  
12          

<br><br>
# 4. word2vec

In [2]:
a = open('yg_input.txt','rb')
sum_pos = pickle.load(a)
sum_pos

pos_sum  \
0       한국 예탁 결제 원 사장 1 일 신년 사 통하 전자 증권 제도 시행 기반 조성 라...   
1       교자 채신 힘 듣 가깝 곳 멀 곳 땔나무 캐 하 늘 의미 다이 행장 올해 과제 전...   
2       대신 증권 한솔 케미칼 최근 인수 자회사 팩스 이익 반영 수익성 강화 삼성전자 양...   
3       1 일 현지 시간 터키 탄불 오르타 이 인근 나이트 클럽 총격 사건 발생 최소 3...   
4       코스 피 상단 밴드 2150 2350 전망 2017 년 정유 증시 밝 주요 증권사...   
5       반도체 성수기 호재 자율 주행 차 등 성장주 유망 유니 동화 기업 평가 되 종목 ...   
6       따르 내년 삼성전자 추가 급등 국내 주요 기업 지주사 전환 잭 이벤트 예고 곽 현...   
7       김 팀장 중국 일대일 미국 인프라 투자 공약 감안 때 금속 중심 원자재 투자 유효...   
8       전문가 신규 장기 대출 받으 고정 금리 선택 기존 변동 금리 대출 받 고정 금리 ...   
9       8 조 원 이상 종합 금융 투자 계좌 개설 부동산 담보 신탁 업무 하 수 있 따르...   
10      임은 영 삼성 증권 연구원 중국 시장 소형차 구매 세 감면 연장 자동차 금융 비중...   
11      삼성 증권 서초 삼성 타운 이전 완료 강남 시대 자산 관리 역량 극대화 금융 계열...   
12      롯데 케미칼 부타디엔 체인 스프레드 확대 따르 이익 성장 전망 상장 조선사 중 재...   
13      양호 수익률 보이 가운데 브라질 주식 펀드 남미 신흥국 주식 펀드 51 315 오...   
14      해외 매출 비중 14 수준 베트남 중심 동남아 사료 시장 진출 하이드 그룹 어류 ...   
15      달러 강세 외국인 자금 국내 시장 이탈 것 김 성환 부국 증권 연구원 달러 부담 ...   
16      민 영화 성공 후 이 행장 개인적 우리 은행장 연임 새 시험대 앞 서 사외 이사 ...   
17      스마트 근무제 가 보수적 은행 조직 정착 수 있 회의적 시선 많 지난해 11 월 ...   
18      작품 시의 오 공동 당선작 정하 한편 수필 늘 성수 기와 비수기 재래시장 마트 차...   
19      더불 전문 사모 집합 투자업 사모 펀드 업 진출 다양 금융 상품 출시 고객 기반 ...   
20      나라 11 월 달러 부족 사태 통화 가치 48 절하 나이 지리 아 화 368 떨어...   
21      달러 향방 예측 위하 트럼프 재정 정책 연 주 금리 인상 시점 관 환 멘트 주시 ...   
22      세계 1 위 수액 기업 박스 터 생명 과학 영양 수액 기술 사 갈 정도 차 대표 ...   
23      트럼프 랠리 마침표 찍 데 트럼프 행정부 출범 앞두 도 트럼프 대통령 당선자 공약...   
24      현대 기아 차 그룹 올해 자율 주행 차 시대 등 대비 기술 개발 총력 기울이 미래...   
25      20161231 뉴스 1 저작권자 뉴스 1 코리 아 무단 전재 배포 금지 머니 투...   
26      민 영화 성공 후 이 행장 개인적 우리 은행장 연임 새 시험대 앞 서 사외 이사 ...   
27      스마트 근무제 가 보수적 은행 조직 정착 수 있 회의적 시선 많 지난해 11 월 ...   
28      작품 시의 오 공동 당선작 정하 한편 수필 늘 성수 기와 비수기 재래시장 마트 차...   
29      더불 전문 사모 집합 투자업 사모 펀드 업 진출 다양 금융 상품 출시 고객 기반 ...   
...                                                  ...   
17649   지난달 말 기준 금리 인상 기대 시장 금리 상승 점 대출 금리 반영 것 보이 27...   
17650   질적 성장 무게 감 두 방침 하 최 연구원 중국 정부 2020 년 금융 리스크 통...   
17651   투자 증권 다음주 올해 마지막 거래 주간 코스 피 밴드 2420 2480 전망 내...   
17652   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17653   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17654   도 트럼프 대통령 이날 크리스마스 연휴 앞두 세제 법안 서명 22 일 현지 시간 ...   
17655   나이스 피 앤 아이 최대 2019 년 건설 근로자 공제 회의 대체 투자 자문 되 ...   
17656   일각 신 회장 실형 받 경우 오너 부재 따르 악재 자금 조달 부정적 영향 끼치 수...   
17657   법원 빠르 시일 내 매각 내년 2 월 초 회생 계획안 하 계획 가지 것 전하 이번...   
17658   당초 연말 서명 늦추 수 있 전망 크리스마스 연휴 앞두 세제 개혁 마무리 미국인 ...   
17659   지난달 말 기준 금리 인상 기대 시장 금리 상승 점 대출 금리 반영 것 보이 27...   
17660   질적 성장 무게 감 두 방침 하 최 연구원 중국 정부 2020 년 금융 리스크 통...   
17661   투자 증권 다음주 올해 마지막 거래 주간 코스 피 밴드 2420 2480 전망 내...   
17662   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17663   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17664   도 트럼프 대통령 이날 크리스마스 연휴 앞두 세제 법안 서명 22 일 현지 시간 ...   
17665   나이스 피 앤 아이 최대 2019 년 건설 근로자 공제 회의 대체 투자 자문 되 ...   
17666   일각 신 회장 실형 받 경우 오너 부재 따르 악재 자금 조달 부정적 영향 끼치 수...   
17667   법원 빠르 시일 내 매각 내년 2 월 초 회생 계획안 하 계획 가지 것 전하 이번...   
17668   당초 연말 서명 늦추 수 있 전망 크리스마스 연휴 앞두 세제 개혁 마무리 미국인 ...   
17669   지난달 말 기준 금리 인상 기대 시장 금리 상승 점 대출 금리 반영 것 보이 27...   
17670   질적 성장 무게 감 두 방침 하 최 연구원 중국 정부 2020 년 금융 리스크 통...   
17671   배당 수익률 상위 종목 산 46 메 리 종 금 증권 46 기업 은행 44 효성 4...   
17672   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17673   2007 년 11 월 후 최저 치 미국 가계 소비 지출 미 경제 3 분 2 차지 ...   
17674   도 트럼프 대통령 이날 크리스마스 연휴 앞두 세제 법안 서명 22 일 현지 시간 ...   
17675   나이스 피 앤 아이 최대 2019 년 건설 근로자 공제 회의 대체 투자 자문 되 ...   
17676   일각 신 회장 실형 받 경우 오너 부재 따르 악재 자금 조달 부정적 영향 끼치 수...   
17677   법원 빠르 시일 내 매각 내년 2 월 초 회생 계획안 하 계획 가지 것 전하 이번...   
17678   당초 연말 서명 늦추 수 있 전망 크리스마스 연휴 앞두 세제 개혁 마무리 미국인 ...   

                                        pos_title  
0                    예탁 결제 원 사장 전자 증권 제도 시행 기반 조성  
1                        덕 훈 행장 조선 등 취약 산업 연착륙 도모  
2                    화학 IT 등 경기 민 감주 주목 업 황 호조 기대  
3                         터키 나이트 클럽 총격 최소 35 명 사망  
4               정 유년 증시 힘차 울 라 대형 주 가격 떨어지 중소형 매력  
5               

In [3]:
len(list(sum_pos.pos_sum) + list(sum_pos.pos_title))

35358

In [4]:
words = []
for word in list(sum_pos.pos_sum) + list(sum_pos.pos_title):
    word = word.split()
    word = [t for t in word if len(t)>0]
    words.append(word)

In [5]:
len(words)

35358

In [6]:
# word2vec model for train set
from gensim.models import Word2Vec
model = Word2Vec(words, size=300, min_count=3, workers=4, sg=1)

C:\Users\SAMSUNG\Anaconda3\lib\site-packages\gensim-2.3.0-py3.5-win-amd64.egg\gensim\utils.py:865: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")
Using TensorFlow backend.


In [7]:
# word2vec embedding vectors for words
w2v_sg = dict(zip(model.wv.index2word, model.wv.syn0))

In [8]:
f = open('w2v_pos_sum.txt', 'wb')
pickle.dump(w2v_sg, f)
f.close()

In [53]:
a = open('w2v_pos_sum.txt','rb')
pickle.load(a)

{'팔라듐': array([-0.14826444, -0.04562946,  0.03536377,  0.2312164 , -0.18628304,
         0.20456924,  0.40511689, -0.40480289,  0.18595795, -0.16973814,
         0.04416042,  0.34099206, -0.24746649,  0.31884444,  0.19397473,
         0.01811224, -0.0199663 ,  0.30021167,  0.05631769, -0.08610792,
         0.41509324,  0.07727005, -0.02820151, -0.25260425, -0.3307361 ,
         0.18941936, -0.04435515, -0.16817147, -0.53963572, -0.47506779,
        -0.09999683,  0.30291831, -0.25793767,  0.34739894, -0.15681922,
         0.27049285, -0.26174647, -0.23444231, -0.07375766, -0.35451141,
         0.30085677, -0.10596266,  0.17265484,  0.42530993, -0.34712857,
        -0.14730304,  0.11399037, -0.18583809,  0.08934533,  0.09000262,
         0.00489308, -0.04544032, -0.27382967, -0.09357274,  0.01559335,
        -0.05472868,  0.14822496,  0.25314394,  0.23557052, -0.30622494,
        -0.012972  , -0.07938886, -0.038399  ,  0.25452045,  0.19051912,
        -0.2657918 , -0.16029128,  0.0078222